# Cypher Queries for Determining Regulatory Paths
*Núria Queralt Rosinach, Andrew Su*

**Queries for the Neo4j guide online**

## Overview
NGLY1 - AQP1 **regulatory review** (*NGLY1 v3.1*)

## Servers 

    * Local: bolt://kylo.scripps.edu:7689
    * AWS: bolt://52.87.232.110:7689

### Imports

In [16]:
from neo4j.v1 import GraphDatabase, basic_auth
import pandas as pd
pd.set_option('display.max_columns', None)  # or 1000
pd.set_option('display.max_rows', None)  # or 1000
pd.set_option('display.max_colwidth', -1)  # or 199

### Functions

In [17]:
def runQuery( driver, query ):
    '''
    This function runs the query onto the database and returns the result.
    in: cypher query string
    out: neo4j query result object
    '''
    
    with driver.session() as session:
        result = session.run('' + query + '')
        
    return result


def parseNode( node ):
    '''
    This function parses the information gathered in the node data structure object resulting after querying neo4j.
        in: node record neo4j object
        out: node as dict
    '''
    
    n = dict()
    n["idx"] = int(node.id)
    n["type"] = list(node.labels)[0]
    n["id"] = str(node.properties['id'])
    n["preflabel"] = str(node.properties['preflabel'])
    n["name"] = str(node.properties['name'])
    n["description"] = str(node.properties['description'])

    return n


def parsePath( path ):
    '''
    This function parsers the information gathered in the path data structure object resulting after querying neo4j.
        in: path record neo4j object
        out: path as dict
    '''
    
    out = {}
    out['Nodes'] = []
    for node in path['path'].nodes:
        n = {}
        n['idx'] = int(node.id)
        n['type'] = list(node.labels)[0]
        n['id'] = str(node.properties['id'])
        n['preflabel'] = str(node.properties['preflabel'])
        n['name'] = str(node.properties['name'])
        n['description'] = str(node.properties['description'])
        out['Nodes'].append(n)
    out['Edges'] = []
    for edge in path['path'].relationships:
        e = {}
        e['idx'] = int(edge.id)
        e['start_node'] = int(edge.start)
        e['end_node'] = int(edge.end)
        e['type'] = str(edge.type)
        e['property_label'] = str(edge.properties['property_label'])
        e['property_uri'] = str(edge.properties['property_uri'])
        e['reference_uri'] = str(edge.properties['reference_uri'])
        e['reference_date'] = str(edge.properties['reference_date'])
        e['reference_supporting_text'] = str(edge.properties['reference_supporting_text'])
        out['Edges'].append(e)
        
    return out

### Initialize neo4j

In [18]:
driver = GraphDatabase.driver("bolt://kylo.scripps.edu:7689", auth=basic_auth("neo4j", "xena"))
#driver = GraphDatabase.driver("bolt://52.87.232.110:7689")

In [ ]:
# Question
## Query topology graph
## Table of summary
## Graph of paths
## Explore paths=> executable cypher query

# NETWORK HYPOTHESES

### Open query to check if they are connected => metapaths
* Are associated at expression level?
    * Are connected through the human transcriptome? -imposing **ONLY** rna genes-

In [7]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(:GENE)-[*..3]-(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*'

        RETURN count(distinct path) as paths
        """
)

# run query
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 2349447
CPU times: user 13.7 ms, sys: 5.2 ms, total: 18.9 ms
Wall time: 6min 47s


**Metapaths:**

In [8]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(:GENE)-[*..3]-(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*'

        RETURN DISTINCT extract (x in rels(path) | type(x)) as types, extract (n in nodes(path) | labels(n)) as labels, length(path) as mp_length, count(distinct path) as paths 
        
        ORDER BY mp_length, paths DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'Nodes': record['labels'], 
                  'Relations': record['types'],
                  'Metapath length': record['mp_length'],
                  'Paths': record['paths']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 20.3 ms, sys: 5.65 ms, total: 25.9 ms
Wall time: 7min 1s


In [9]:
res_df

Metapath length                                     Nodes    Paths  \
0    2                [[GENE], [GENE], [GENE]]                  7         
1    3                [[GENE], [GENE], [GENE], [GENE]]          5120      
2    3                [[GENE], [GENE], [ANAT], [GENE]]          2564      
3    3                [[GENE], [GENE], [PHYS], [GENE]]          936       
4    3                [[GENE], [GENE], [PHYS], [GENE]]          504       
5    3                [[GENE], [GENE], [GENE], [GENE]]          162       
6    3                [[GENE], [GENE], [PHYS], [GENE]]          110       
7    3                [[GENE], [GENE], [GENE], [GENE]]          80        
8    3                [[GENE], [GENE], [DISO], [GENE]]          64        
9    3                [[GENE], [GENE], [GENE], [GENE]]          30        
10   3                [[GENE], [GENE], [GENE], [GENE]]          20        
11   3                [[GENE], [GENE], [DISO], [GENE]]          8         
12   3                [[GENE], [GENE], [PHYS], [GENE]]          4         
13   3                [[GENE], [GENE], [PHYS], [GENE]]          3         
14   3                [[GENE], [GENE], [PHYS], [GENE]]          2         
15   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  1325710   
16   4                [[GENE], [GENE], [GENE], [ANAT], [GENE]]  269752    
17   4                [[GENE], [GENE], [ANAT], [GENE], [GENE]]  144315    
18   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  106135    
19   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  92769     
20   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  49888     
21   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  46316     
22   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  26512     
23   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  23147     
24   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  21681     
25   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  19472     
26   4                [[GENE], [GENE], [GENE], [ANAT], [GENE]]  18820     
27   4                [[GENE], [GENE], [GENE], [ANAT], [GENE]]  18428     
28   4                [[GENE], [GENE], [DISO], [PHYS], [GENE]]  16574     
29   4                [[GENE], [GENE], [GENE], [DISO], [GENE]]  16408     
30   4                [[GENE], [GENE], [ANAT], [GENE], [GENE]]  15694     
31   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  15033     
32   4                [[GENE], [GENE], [DISO], [GENE], [GENE]]  14840     
33   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  9257      
34   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  8674      
35   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  8239      
36   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  6676      
37   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  6284      
38   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  6028      
39   4                [[GENE], [GENE], [DISO], [PHYS], [GENE]]  4939      
40   4                [[GENE], [GENE], [ANAT], [GENE], [GENE]]  4104      
41   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  3666      
42   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  3518      
43   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  2857      
44   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  2824      
45   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  2648      
46   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  2558      
47   4                [[GENE], [GENE], [DISO], [DISO], [GENE]]  2530      
48   4                [[GENE], [GENE], [ANAT], [GENE], [GENE]]  2130      
49   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  1632      
50   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  1626      
51   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  1596      
52   4                [[GENE],

* Are associated at expression level?
    * Are connected through the human transcriptome? -imposing rna genes **AND** regulatory edges-

In [11]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(:GENE)-[*..3]-(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0

        RETURN count(distinct path) as paths
        """
)

# run query
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 932233
CPU times: user 14.5 ms, sys: 5.29 ms, total: 19.8 ms
Wall time: 7min 52s


**Metapaths:**

In [12]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(:GENE)-[*..3]-(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0

        RETURN DISTINCT extract (x in rels(path) | type(x)) as types, extract (n in nodes(path) | labels(n)) as labels, length(path) as mp_length, count(distinct path) as paths 
        
        ORDER BY mp_length, paths DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'Nodes': record['labels'], 
                  'Relations': record['types'],
                  'Metapath length': record['mp_length'],
                  'Paths': record['paths']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 19.6 ms, sys: 4.6 ms, total: 24.2 ms
Wall time: 8min 10s


In [13]:
res_df

Metapath length                                     Nodes   Paths  \
0   2                [[GENE], [GENE], [GENE]]                  3        
1   3                [[GENE], [GENE], [GENE], [GENE]]          2560     
2   3                [[GENE], [GENE], [GENE], [GENE]]          20       
3   3                [[GENE], [GENE], [GENE], [GENE]]          20       
4   3                [[GENE], [GENE], [GENE], [GENE]]          10       
5   3                [[GENE], [GENE], [GENE], [GENE]]          10       
6   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  754924   
7   4                [[GENE], [GENE], [GENE], [ANAT], [GENE]]  50195    
8   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  19962    
9   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  19648    
10  4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  17121    
11  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  14200    
12  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  11196    
13  4                [[GENE], [GENE], [ANAT], [GENE], [GENE]]  9717     
14  4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  7841     
15  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  7445     
16  4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  3795     
17  4                [[GENE], [GENE], [GENE], [DISO], [GENE]]  3298     
18  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  2202     
19  4                [[GENE], [GENE], [DISO], [GENE], [GENE]]  1760     
20  4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  1735     
21  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  1381     
22  4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  588      
23  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  536      
24  4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  245      
25  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  228      
26  4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  178      
27  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  164      
28  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  152      
29  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  136      
30  4                [[GENE], [GENE], [GENE], [DISO], [GENE]]  98       
31  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  88       
32  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  88       
33  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  88       
34  4                [[GENE], [GENE], [DISO], [GENE], [GENE]]  87       
35  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  80       
36  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  80       
37  4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  74       
38  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  64       
39  4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  52       
40  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  40       
41  4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  39       
42  4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  33       
43  4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  19       
44  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  12       
45  4                [[GENE], [GENE], [DISO], [GENE], [GENE]]  11       
46  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  8        
47  4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  2        

                                                 Relations  
0   [RO:0002434, RO:0002434]                                
1   [RO:0002434, RO:0002434, RO:0002434]                    
2   [RO:0002434, RO:0002435, RO:0002434]                    
3   [RO:0002434, RO:0002325, RO:0002434]                    
4   [RO:0002434, RO:HOM0000011, RO:0002434]                 
5   [RO:0002434, RO:0002434, RO:HOM0000011]                 

* Are associated at expression level?
    * Are connected through TFs? -imposing **ONLY** regulatory edges-

In [27]:
%%time
query = (
        """
        MATCH path=(source:GENE)--()-[*..3]-(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND size(interactions) <> 0

        RETURN count(distinct path) as paths
        """
)

# run query
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 1051945
CPU times: user 8.48 ms, sys: 11.9 ms, total: 20.3 ms
Wall time: 8min 36s


**Metapaths:**

In [28]:
%%time
query = (
        """
        MATCH path=(source:GENE)--()-[*..3]-(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND size(interactions) <> 0

        RETURN DISTINCT extract (x in rels(path) | type(x)) as types, extract (n in nodes(path) | labels(n)) as labels, length(path) as mp_length, count(distinct path) as paths 
        
        ORDER BY mp_length, paths DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'Nodes': record['labels'], 
                  'Relations': record['types'],
                  'Metapath length': record['mp_length'],
                  'Paths': record['paths']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 25.4 ms, sys: 5.71 ms, total: 31.1 ms
Wall time: 9min


In [29]:
res_df

Metapath length                                     Nodes   Paths  \
0    2                [[GENE], [GENE], [GENE]]                  3        
1    3                [[GENE], [GENE], [GENE], [GENE]]          2666     
2    3                [[GENE], [GENE], [GENE], [GENE]]          20       
3    3                [[GENE], [GENE], [GENE], [GENE]]          20       
4    3                [[GENE], [GENE], [GENE], [GENE]]          18       
5    3                [[GENE], [GENE], [GENE], [GENE]]          10       
6    3                [[GENE], [ANAT], [GENE], [GENE]]          8        
7    3                [[GENE], [DISO], [GENE], [GENE]]          8        
8    3                [[GENE], [GENE], [ANAT], [GENE]]          5        
9    3                [[GENE], [PHYS], [GENE], [GENE]]          3        
10   3                [[GENE], [GENE], [GENE], [GENE]]          2        
11   3                [[GENE], [PHYS], [GENE], [GENE]]          1        
12   3                [[GENE], [PHYS], [GENE], [GENE]]          1        
13   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  823995   
14   4                [[GENE], [GENE], [GENE], [ANAT], [GENE]]  52502    
15   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  22746    
16   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  21018    
17   4                [[GENE], [ANAT], [GENE], [GENE], [GENE]]  18667    
18   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  17901    
19   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  14858    
20   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  12802    
21   4                [[GENE], [GENE], [ANAT], [GENE], [GENE]]  10170    
22   4                [[GENE], [DISO], [GENE], [GENE], [GENE]]  9401     
23   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  8319     
24   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  7735     
25   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  3990     
26   4                [[GENE], [GENE], [GENE], [DISO], [GENE]]  3444     
27   4                [[GENE], [PHYS], [GENE], [GENE], [GENE]]  2914     
28   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  2538     
29   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  2202     
30   4                [[GENE], [GENE], [DISO], [GENE], [GENE]]  1972     
31   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  1949     
32   4                [[GENE], [PHYS], [GENE], [GENE], [GENE]]  1760     
33   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  1481     
34   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  652      
35   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  640      
36   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  424      
37   4                [[GENE], [PHYS], [GENE], [GENE], [GENE]]  418      
38   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  296      
39   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  282      
40   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  228      
41   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  210      
42   4                [[GENE], [ANAT], [GENE], [GENE], [GENE]]  208      
43   4                [[GENE], [ANAT], [GENE], [GENE], [GENE]]  174      
44   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  164      
45   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  160      
46   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  144      
47   4                [[GENE], [DISO], [GENE], [GENE], [GENE]]  144      
48   4                [[GENE], [VARI], [DISO], [GENE], [GENE]]  136      
49   4                [[GENE], [GENE], [DISO], [PHYS], [GENE]]  113      
50   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  108      
51   4                [[GENE], [PHYS], [GENE], [GENE], [GENE]]  106      
52   4                [[GENE], [ANAT], [GENE], [GENE], [GENE]]  104      
53   4   

* Are associated at expression level?
    * Are connected through TFs or expression genes? -imposing rna genes **OR** regulatory edges-

In [30]:
%%time
query = (
        """
        MATCH path=(source:GENE)--()-[*..3]-(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*freeze.*|.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND size(interactions) <> 0

        RETURN count(distinct path) as paths
        """
)

# run query
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 2469159
CPU times: user 16.3 ms, sys: 4.11 ms, total: 20.4 ms
Wall time: 9min


**Metapaths:**

In [31]:
%%time
query = (
        """
        MATCH path=(source:GENE)--()-[*..3]-(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*freeze.*|.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND size(interactions) <> 0

        RETURN DISTINCT extract (x in rels(path) | type(x)) as types, extract (n in nodes(path) | labels(n)) as labels, length(path) as mp_length, count(distinct path) as paths 
        
        ORDER BY mp_length, paths DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'Nodes': record['labels'], 
                  'Relations': record['types'],
                  'Metapath length': record['mp_length'],
                  'Paths': record['paths']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 27.8 ms, sys: 7.4 ms, total: 35.2 ms
Wall time: 9min 52s


In [32]:
res_df

Metapath length                                     Nodes    Paths  \
0    2                [[GENE], [GENE], [GENE]]                  7         
1    3                [[GENE], [GENE], [GENE], [GENE]]          5226      
2    3                [[GENE], [GENE], [ANAT], [GENE]]          2569      
3    3                [[GENE], [GENE], [PHYS], [GENE]]          936       
4    3                [[GENE], [GENE], [PHYS], [GENE]]          504       
5    3                [[GENE], [GENE], [GENE], [GENE]]          170       
6    3                [[GENE], [GENE], [PHYS], [GENE]]          110       
7    3                [[GENE], [GENE], [GENE], [GENE]]          80        
8    3                [[GENE], [GENE], [DISO], [GENE]]          64        
9    3                [[GENE], [GENE], [GENE], [GENE]]          30        
10   3                [[GENE], [GENE], [GENE], [GENE]]          20        
11   3                [[GENE], [ANAT], [GENE], [GENE]]          8         
12   3                [[GENE], [DISO], [GENE], [GENE]]          8         
13   3                [[GENE], [GENE], [DISO], [GENE]]          8         
14   3                [[GENE], [GENE], [PHYS], [GENE]]          4         
15   3                [[GENE], [PHYS], [GENE], [GENE]]          3         
16   3                [[GENE], [GENE], [PHYS], [GENE]]          3         
17   3                [[GENE], [GENE], [GENE], [GENE]]          2         
18   3                [[GENE], [GENE], [PHYS], [GENE]]          2         
19   3                [[GENE], [PHYS], [GENE], [GENE]]          1         
20   3                [[GENE], [PHYS], [GENE], [GENE]]          1         
21   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  1394781   
22   4                [[GENE], [GENE], [GENE], [ANAT], [GENE]]  272059    
23   4                [[GENE], [GENE], [ANAT], [GENE], [GENE]]  144768    
24   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  106613    
25   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  93549     
26   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  52986     
27   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  47372     
28   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  28118     
29   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  23342     
30   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  21971     
31   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  20130     
32   4                [[GENE], [GENE], [GENE], [ANAT], [GENE]]  18914     
33   4                [[GENE], [ANAT], [GENE], [GENE], [GENE]]  18667     
34   4                [[GENE], [GENE], [GENE], [ANAT], [GENE]]  18482     
35   4                [[GENE], [GENE], [DISO], [PHYS], [GENE]]  16687     
36   4                [[GENE], [GENE], [GENE], [DISO], [GENE]]  16554     
37   4                [[GENE], [GENE], [ANAT], [GENE], [GENE]]  15706     
38   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  15070     
39   4                [[GENE], [GENE], [DISO], [GENE], [GENE]]  15052     
40   4                [[GENE], [DISO], [GENE], [GENE], [GENE]]  9401      
41   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  9261      
42   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  8680      
43   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  8453      
44   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  6690      
45   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  6284      
46   4                [[GENE], [GENE], [PHYS], [GENE], [GENE]]  6080      
47   4                [[GENE], [GENE], [DISO], [PHYS], [GENE]]  4970      
48   4                [[GENE], [GENE], [ANAT], [GENE], [GENE]]  4108      
49   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  4002      
50   4                [[GENE], [GENE], [GENE], [PHYS], [GENE]]  3518      
51   4                [[GENE], [GENE], [GENE], [GENE], [GENE]]  2957      
52   4                [[GENE],

### Specific query template with > 1000 paths => results viz in a summary table
Query template to answer the connection at expression level.



* Looking for **gene interactors** between RNA genes and TFs of AQP1 ( L=3 )

In [35]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(:GENE)-[:`RO:0002434`]-(:GENE)-[:`RO:0002434`]->(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0

        RETURN count(distinct path) as paths
        """
)

# run query
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 2328
CPU times: user 2.45 ms, sys: 0 ns, total: 2.45 ms
Wall time: 2.81 s


In [36]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002434`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,rna,tf,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0

        RETURN count(distinct rna) as rnas, count(distinct tf) as tfs, count(distinct path) as paths
        
        ORDER BY paths DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'Expressed_genes': record['rnas'], 
                  'TFs': record['tfs'],
                  'Paths': record['paths']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 2.94 ms, sys: 0 ns, total: 2.94 ms
Wall time: 2.86 s


In [37]:
res_df

Expressed_genes  Paths  TFs
0  894              2328   31

In [40]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002434`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,rna,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0

        RETURN DISTINCT rna.name, count(distinct path) as paths
        
        ORDER BY paths DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'Expressed_gene_name': record['rna.name'], 
                  'Paths': record['paths']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 16.6 ms, sys: 0 ns, total: 16.6 ms
Wall time: 2.9 s


In [41]:
res_df

Expressed_gene_name  \
0    MYC associated zinc finger protein                                                                    
1    SMAD family member 3                                                                                  
2    ELK1, ETS transcription factor                                                                        
3    paired like homeodomain 2                                                                             
4    melanogenesis associated transcription factor                                                         
5    transcription factor AP-2 gamma                                                                       
6    signal transducer and activator of transcription 1                                                    
7    HIC ZBTB transcriptional repressor 1                                                                  
8    activating transcription factor 3                                                                     
9    heat shock transcription factor 2                                                                     
10   transcription factor 4                                                                                
11   nuclear receptor subfamily 2 group F member 2                                                         
12   cyclin D1                                                                                             
13   SMAD family member 1                                                                                  
14   zinc finger protein 148                                                                               
15   transcription factor 7                                                                                
16   recombination signal binding protein for immunoglobulin kappa J region                                
17   hes family bHLH transcription factor 1                                                                
18   early growth response 3                                                                               
19   forkhead box O3                                                                                       
20   paired box 3                                                                                          
21   paired related homeobox 1                                                                             
22   msh homeobox 1                                                                                        
23   early B cell factor 1                                                                                 
24   E74 like ETS transcription factor 1                                                                   
25   aryl hydrocarbon receptor                                                                             
26   FOS like 2, AP-1 transcription factor subunit                                                         
27   RB transcriptional corepressor 1                                                                      
28   hypoxia inducible factor 1 subunit alpha                                                              
29   interferon regulatory factor 4                                                                        
30   ELK3, ETS transcription factor                                                                        
31   TSC22 domain family member 1                                                                          
32   GATA binding protein 2                                                                                
33   TOP1 binding arginine/serine rich protein                                                             
34   engrailed homeobox 1                                                                                  
35   CDC42 effector protein 3                                                                              
36   insulin like growth factor 1 receptor                                               

In [42]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002434`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,tf,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0

        RETURN DISTINCT tf.name, count(distinct path) as paths
        
        ORDER BY paths DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'TF_name': record['tf.name'], 
                  'Paths': record['paths']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 3.69 ms, sys: 0 ns, total: 3.69 ms
Wall time: 2.86 s


In [43]:
res_df

Paths                                                TF_name
0   460    lymphoid enhancer binding factor 1                   
1   383    tumor protein p53                                    
2   363    MYC associated zinc finger protein                   
3   282    transcription regulator                              
4   161    twin-arginine translocase TatA/TatE family subunit   
5   133    myocyte enhancer factor 2A                           
6   124    TATA-box binding protein                             
7   114    mitochondrial elongation factor G- like protein      
8   107    Fos proto-oncogene, AP-1 transcription factor subunit
9   70     transcription factor 4                               
10  55     GATA binding protein 6                               
11  26     IKAROS family zinc finger 2                          
12  21     hypothetical protein                                 
13  3      cysteine and serine rich nuclear protein 1           
14  3      glycerol kinase                                      
15  2      notch 2 N-terminal like                              
16  2      midline 2                                            
17  2      tyrosine kinase non receptor 2                       
18  2      sprouty RTK signaling antagonist 2                   
19  2      cAMP responsive element binding protein 3            
20  2      centrosomal protein 44                               
21  2      coiled-coil domain containing 85B                    
22  1      cartilage acidic protein 1                           
23  1      IKAROS family zinc finger 3                          
24  1      regulator of G protein signaling 17                  
25  1      EGF containing fibulin extracellular matrix protein 2
26  1      tripartite motif containing 23                       
27  1      glycerol kinase 5                                    
28  1      MyoD family inhibitor                                
29  1      ADAMTS like 4                                        
30  1      lamin A/C

In [47]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[i2:`RO:0002434`]-(tf:GENE)-[i3:`RO:0002434`]->(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,i2,i3,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0

        RETURN DISTINCT i1.reference_supporting_text AS Prov1, i2.reference_supporting_text AS Prov2, i3.reference_supporting_text AS Prov3, count(distinct path) as paths
        
        ORDER BY paths DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'Provenance_i1': record['Prov1'], 
                  'Provenance_i2': record['Prov2'], 
                  'Provenance_i3': record['Prov3'], 
                  'Paths': record['paths']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 3.44 ms, sys: 0 ns, total: 3.44 ms
Wall time: 3.01 s


In [48]:
res_df

Paths  \
0   1363    
1   282     
2   146     
3   120     
4   106     
5   74      
6   69      
7   40      
8   30      
9   30      
10  27      
11  13      
12  10      
13  9       
14  5       
15  4       

                                                                         Provenance_i1  \
0   This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
1   This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
2   This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
3   This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
4   This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
5   This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
6   This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
7   This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
8   This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
9   This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
10  This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
11  This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
12  This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
13  This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
14  This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   
15  This edge comes from the RNA-seq profile dataset extracted by the Freeze Lab 2018.   

                                                                 Provenance_i2  \
0   This edge comes from the C3:TFT dataset in "msigdb" source.                  
1   This edge comes from the Monarch Knowledge Graph 2018.                       
2   This edge comes from the NEPH2012 dataset in "tftargets" source.             
3   This edge comes from the Monarch Knowledge Graph 2018.                       
4   This edge comes from the NEPH2012 dataset in "tftargets" source.             
5   This edge comes from the C3:TFT dataset in "msigdb" source.                  
6   This edge comes from the ENCODE_ENCFF001UUQ dataset in "tftargets" source.   
7   This edge comes from the TRED dataset in "tftargets" source.                 
8   This edge comes from the ENCODE_ENCFF001UUQ dataset in "tftargets" source.   
9   This edge comes from the NEPH2012 dataset in "tftargets" source.             
10  This edge comes from the TRRUST dataset in "tftargets" source.               
11  This edge comes from the TRRUST dataset in "tftargets" source.               
12  This edge comes from the TRRUST dataset in "tftargets" source.               
13  This edge comes from the TRED dataset in "tftargets" source.                 
14  This edge comes from the TRED dataset in "tftargets" source.                 
15  This edge comes from the C3:TFT dataset in "msigdb" source.                  

                                                   Provenance_i3  
0   This edge comes from the C3:TFT dataset in "msigdb" source.   
1   This edge comes from the TRED dataset in "tftargets" source.  
2   This edge comes from the C3:TFT dataset in "msigdb" source.   
3   This edge comes from the C3:TFT dataset in "msigdb" source.   
4   This edge comes from the Monarch Knowledge Graph 2018.        
5   This edge comes from the Monarch Knowledge Graph 2018.        
6   This edge comes from the C3:TFT dataset in "msigdb" source.   
7   This edge comes from the TRED dataset in "tftargets" source.  
8   This edge comes from the Monarch Knowledge Graph 2018.        
9   This edge comes from the TRED dataset in "tftargets" source.  
10  This edge comes from the TRED dataset in "tftargets" source.  
11  This edge comes from the Monarch Knowledge Graph

In [49]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[i2:`RO:0002434`]-(tf:GENE)-[i3:`RO:0002434`]->(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,i2,i3,rna,tf,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0

        RETURN DISTINCT i1.reference_supporting_text AS Prov1, rna.name, i2.reference_supporting_text AS Prov2, tf.name, i3.reference_supporting_text AS Prov3, count(distinct path) as paths
        
        ORDER BY paths DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'Provenance_i1': record['Prov1'], 
                  'Expressed_gene_name': record['rna.name'],
                  'Provenance_i2': record['Prov2'],
                  'TF_name': record['tf.name'],
                  'Provenance_i3': record['Prov3'], 
                  'Paths': record['paths']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 79.2 ms, sys: 2.91 ms, total: 82.1 ms
Wall time: 3 s


In [50]:
res_df

Expressed_gene_name  \
0     proliferating cell nuclear antigen                                                                    
1     lysine acetyltransferase 2B                                                                           
2     StAR related lipid transfer domain containing 10                                                      
3     argonaute 2, RISC catalytic component                                                                 
4     transcription factor AP-2 gamma                                                                       
5     USO1 vesicle transport factor                                                                         
6     ELK1, ETS transcription factor                                                                        
7     ribonucleoprotein, PTB binding 1                                                                      
8     insulin like growth factor 2 mRNA binding protein 1                                                   
9     HIC ZBTB transcriptional repressor 1                                                                  
10    metastasis associated 1 family member 3                                                               
11    heterogeneous nuclear ribonucleoprotein A2/B1                                                         
12    cyclin D1                                                                                             
13    ribosomal protein L24                                                                                 
14    keratin 19                                                                                            
15    STEAP3 metalloreductase                                                                               
16    integrin subunit beta 1                                                                               
17    tripartite motif containing 32                                                                        
18    cyclin D binding myb like transcription factor 1                                                      
19    insulin like growth factor 2 mRNA binding protein 3                                                   
20    msh homeobox 1                                                                                        
21    matrix metallopeptidase 2                                                                             
22    matrix metallopeptidase 2                                                                             
23    mitochondrial ribosomal protein S18B                                                                  
24    transcription factor AP-2 gamma                                                                       
25    forkhead box K1                                                                                       
26    recombination signal binding protein for immunoglobulin kappa J region                                
27    glycerophosphodiester phosphodiesterase 1                                                             
28    interferon regulatory factor 4                                                                        
29    ribosomal protein L23a                                                                                
30    crystallin alpha B                                                                                    
31    RNA binding motif protein 3                                                                           
32    cytoskeleton associated protein 4                                                                     
33    engrailed homeobox 1                                                                                  
34    interferon regulatory factor 6                                                                        
35    casein kinase 1 gamma 3                                                                               
36    proteasome activator subunit 4                 

In [51]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[i2:`RO:0002434`]-(tf:GENE)-[i3:`RO:0002434`]->(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,i2,i3,rna,tf,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0

        RETURN DISTINCT rna.name, i2.reference_supporting_text AS Prov2, tf.name, count(distinct path) as paths
        
        ORDER BY paths DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'Expressed_gene_name': record['rna.name'],
                  'Provenance_i2': record['Prov2'],
                  'TF_name': record['tf.name'],
                  'Paths': record['paths']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 59.9 ms, sys: 0 ns, total: 59.9 ms
Wall time: 2.96 s


In [52]:
res_df

Expressed_gene_name  \
0     SP100 nuclear antigen                                                                                 
1     aryl hydrocarbon receptor                                                                             
2     ubiquitin specific peptidase 15                                                                       
3     ATR serine/threonine kinase                                                                           
4     cyclin D1                                                                                             
5     lysine acetyltransferase 2B                                                                           
6     USO1 vesicle transport factor                                                                         
7     transcription factor 7 like 1                                                                         
8     protein arginine methyltransferase 1                                                                  
9     ENAH, actin regulator                                                                                 
10    annexin A7                                                                                            
11    SWI/SNF related, matrix associated, actin dependent regulator of chromatin subfamily c member 1       
12    metastasis associated 1 family member 3                                                               
13    HECT and RLD domain containing E3 ubiquitin protein ligase 5                                          
14    ubiquitin like with PHD and ring finger domains 2                                                     
15    transcription factor AP-2 gamma                                                                       
16    integrin subunit beta 1                                                                               
17    nuclear receptor coactivator 3                                                                        
18    glycerophosphodiester phosphodiesterase 1                                                             
19    heat shock transcription factor 2                                                                     
20    SLC2A4 regulator                                                                                      
21    hes family bHLH transcription factor 1                                                                
22    COP1, E3 ubiquitin ligase                                                                             
23    calcium/calmodulin dependent protein kinase IV                                                        
24    zinc finger protein 148                                                                               
25    insulin like growth factor 2 mRNA binding protein 1                                                   
26    anti-silencing function 1A histone chaperone                                                          
27    matrix metallopeptidase 2                                                                             
28    MYC associated zinc finger protein                                                                    
29    protein phosphatase 3 catalytic subunit gamma                                                         
30    SMAD family member 1                                                                                  
31    SWI/SNF related, matrix associated, actin dependent regulator of chromatin, subfamily a, member 5     
32    STEAP3 metalloreductase                                                                               
33    nuclear receptor subfamily 2 group F member 2                                                         
34    N-myristoyltransferase 2                                                                              
35    ribosomal protein L37a                                                                                
36    TP53 induced glycolysis regulatory phosphatase 

### Specific query template with < 1000 paths => results viz graphically
Query template to answer the connection at expression level.

In [34]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(:GENE)-[:`RO:0002435`]-(:GENE)-[:`RO:0002434`]->(target:GENE)

        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0

        RETURN count(distinct path) as paths
        """
)

# run query: `genetically interacts with` OR `RO:0002435`
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 20
CPU times: user 0 ns, sys: 1.91 ms, total: 1.91 ms
Wall time: 1.19 s


we could do the above query but with `colocalizes with` or `RO:0002325`

---
## Question 2
Input rna + tf genes interactors to look for NGLY1 phenotypes

In [66]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002435`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)
        
        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,rna,tf,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0      

        WITH COLLECT(DISTINCT rna.id) + COLLECT(DISTINCT tf.id) AS genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(:DISO)--(g:GENE)
        
        WHERE g.id in genes
        
        RETURN count(distinct path) as paths
        """
)

# run query: `genetically interacts with` OR `RO:0002435`
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 21
CPU times: user 0 ns, sys: 2.03 ms, total: 2.03 ms
Wall time: 1.38 s


In [71]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002435`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)
        
        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,rna,tf,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0      

        WITH COLLECT(DISTINCT rna.id) + COLLECT(DISTINCT tf.id) AS genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(ph:DISO)--(g:GENE)
        
        WHERE g.id in genes AND ph.id CONTAINS 'HP:'
        
        RETURN DISTINCT ph.id AS phenotype_id, ph.preflabel AS phenotype_label, COLLECT(DISTINCT g.name) AS gene_id_list, count(DISTINCT g.id) AS genes
        
        ORDER BY genes DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'phenotype_label': record['phenotype_label'],
                  'phenotype_id': record['phenotype_id'],
                  'gene_id_list': record['gene_id_list'],
                  'genes': record['genes']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 2.45 ms, sys: 1.11 ms, total: 3.56 ms
Wall time: 1.45 s


In [72]:
res_df

gene_id_list  \
0  [STT3B, catalytic subunit of the oligosaccharyltransferase complex, kinesin family member 2A, tumor protein p53]   
1  [STT3B, catalytic subunit of the oligosaccharyltransferase complex, kinesin family member 2A]                      
2  [STT3B, catalytic subunit of the oligosaccharyltransferase complex, kinesin family member 2A]                      
3  [STT3B, catalytic subunit of the oligosaccharyltransferase complex, kinesin family member 2A]                      
4  [STT3B, catalytic subunit of the oligosaccharyltransferase complex]                                                
5  [STT3B, catalytic subunit of the oligosaccharyltransferase complex]                                                
6  [tumor protein p53]                                                                                                
7  [tumor protein p53]                                                                                                
8  [tumor protein p53]                                                                                                
9  [STT3B, catalytic subunit of the oligosaccharyltransferase complex]                                                

   genes phenotype_id                  phenotype_label  
0  3      HP:0001250   epileptic seizure                
1  2      HP:0001263   Developmental disability         
2  2      HP:0000252   microcephaly                     
3  2      HP:0001511   Intrauterine growth retardation  
4  1      HP:0001249   intellectual disability          
5  1      HP:0000648   optic atrophy                    
6  1      HP:0002015   Premature spillage               
7  1      HP:0002910   Elevated transaminases           
8  1      HP:0001310   Dysmetria                        
9  1      HP:0001272   Cerebellar atrophy

* interacts with

In [73]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002434`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)
        
        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,rna,tf,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0      

        WITH COLLECT(DISTINCT rna.id) + COLLECT(DISTINCT tf.id) AS genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(:DISO)--(g:GENE)
        
        WHERE g.id in genes
        
        RETURN count(distinct path) as paths
        """
)

# run query: `genetically interacts with` OR `RO:0002435`
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 1286
CPU times: user 2.59 ms, sys: 0 ns, total: 2.59 ms
Wall time: 16.4 s


In [74]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002434`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)
        
        WHERE source.id = 'HGNC:17646' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,rna,tf,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_supporting_text) =~ '.*freeze.*' AND size(interactions) <> 0      

        WITH COLLECT(DISTINCT rna.id) + COLLECT(DISTINCT tf.id) AS genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(ph:DISO)--(g:GENE)
        
        WHERE g.id in genes AND ph.id CONTAINS 'HP:'
        
        RETURN DISTINCT ph.id AS phenotype_id, ph.preflabel AS phenotype_label, COLLECT(DISTINCT g.name) AS gene_id_list, count(DISTINCT g.id) AS genes
        
        ORDER BY genes DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'phenotype_label': record['phenotype_label'],
                  'phenotype_id': record['phenotype_id'],
                  'gene_id_list': record['gene_id_list'],
                  'genes': record['genes']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 8.12 ms, sys: 0 ns, total: 8.12 ms
Wall time: 15.2 s


In [75]:
res_df

gene_id_list  \
0   [glutamate ionotropic receptor AMPA type subunit 3, erythrocyte membrane protein band 4.1 like 1, receptor interacting serine/threonine kinase 4, WD repeat domain 11, DNA ligase 4, recombination signal binding protein for immunoglobulin kappa J region, immunoglobulin binding protein 1, serologically defined colon cancer antigen 8, heterogeneous nuclear ribonucleoprotein A1, AKT serine/threonine kinase 3, dopey family member 1, tetratricopeptide repeat domain 8, ATRX, chromatin remodeler, solute carrier family 25 member 22, GNAS complex locus, transducin beta like 1 X-linked receptor 1, SBDS, ribosome maturation factor, ribonucleotide reductase regulatory TP53 inducible subunit M2B, zinc finger E-box binding homeobox 2, TOP1 binding arginine/serine rich protein, heparan sulfate 6-O-sulfotransferase 1, OPA3, outer mitochondrial membrane lipid metabolism regulator, GATA binding protein 6, L1 cell adhesion molecule, phosphatidylinositol glycan anchor biosynthesis class O, elastin, midline 2, phosphoglycerate dehydrogenase, nectin cell adhesion molecule 1, ATPase H+ transporting V1 subunit E1, gap junction protein alpha 1, GLI family zinc finger 2, EGF domain specific O-linked N-acetylglucosamine transferase, twist family bHLH transcription factor 2, insulin like growth factor 1 receptor, SPARC related modular calcium binding 1, FA complementation group E, RWD domain containing 2A, RB binding protein 8, endonuclease, ephrin B1, ATR serine/threonine kinase, calcium/calmodulin dependent serine protein kinase, Meis homeobox 2, component of oligomeric golgi complex 6, glypican 6, retinoic acid receptor beta, acyl-CoA synthetase long chain family member 4, latent transforming growth factor beta binding protein 2, damage specific DNA binding protein 2, paired box 3, patched 1, tripartite motif containing 32, lamin A/C, MRE11 homolog, double strand break repair nuclease, prosaposin, FAST kinase domains 2, RAS p21 protein activator 2, ubiquitin protein ligase E3A, ERCC excision repair 6 like 2, SRY-box 11, RAD50 double strand break repair protein, integrin subunit alpha 7, paired like homeodomain 1, B cell CLL/lymphoma 11B, MAF bZIP transcription factor B, heterogeneous nuclear ribonucleoprotein A2/B1, glycerol kinase, p21 (RAC1) activated kinase 3, Fos proto-oncogene, AP-1 transcription factor subunit, enhancer of polycomb homolog 2, ETS2 repressor factor, glutamate decarboxylase 1, glutamate ionotropic receptor kainate type subunit 2, pyruvate carboxylase, ADP ribosylation factor guanine nucleotide exchange factor 1, eukaryotic translation initiation factor 2 alpha kinase 3, ribosomal protein S6 kinase A3, nibrin, zinc finger protein 148, DCC netrin 1 receptor, phosphatidylinositol-4,5-bisphosphate 3-kinase catalytic subunit alpha, ADAMTS like 4, zinc finger and BTB domain containing 20, neural precursor cell expressed, developmentally down-regulated 4-like, E3 ubiquitin protein ligase, nucleus accumbens associated 1]   
1   [DNA ligase 4, neural precursor cell expressed, developmentally down-regulated 4-like, E3 ubiquitin protein ligase, pyruvate carboxylase, glutamate ionotropic receptor AMPA type subunit 3, TATA-box binding protein, GNAS complex locus, zinc finger and BTB domain containing 20, solute carrier family 25 member 22, component of oligomeric golgi complex 6, DCC netrin 1 receptor, echinoderm microtubule associated protein like 1, glutamate ionotropic receptor NMDA type subunit 2D, L1 cell adhesion molecule, GATA binding protein 6, calcium/calmodulin dependent serine protein kinase, WD repeat domain 11, ANKH inorganic pyrophosphate transport regulator, ATPase H+ transporting V1 subunit E1, brain derived neurotrophic factor, amyloid beta precursor protein, GLI family zinc finger 2, ATRX, chromatin remodeler, midline 2, RAN binding protein 2, ADAMTS like 4, programmed cell death 10, glutamate decarboxylase 1, glutamate ionotropic receptor kainate type subunit 2, thymidine kinase 2, mitochondrial, damage spe

---

In [59]:
%%time
query = (
        """
        MATCH (source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002435`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)

        WITH COLLECT(DISTINCT rna.id) + COLLECT(DISTINCT tf.id) AS genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(:DISO)--(g:GENE)
        
        WHERE g.id in genes
        
        RETURN count(distinct path) as paths
        """
)

# run query: `genetically interacts with` OR `RO:0002435`
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 1519
CPU times: user 6.66 ms, sys: 3.41 ms, total: 10.1 ms
Wall time: 4min 4s


In [61]:
%%time
query = (
        """
        MATCH (source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002435`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)

        WITH COLLECT(DISTINCT rna.id) AS genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(:DISO)--(g:GENE)
        
        WHERE g.id in genes
        
        RETURN count(distinct path) as paths
        """
)

# run query: `genetically interacts with` OR `RO:0002435`
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 1519
CPU times: user 2.45 ms, sys: 5.47 ms, total: 7.92 ms
Wall time: 2min 58s


In [62]:
%%time
query = (
        """
        MATCH (source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002435`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)

        WITH COLLECT(DISTINCT tf.id) AS genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(:DISO)--(g:GENE)
        
        WHERE g.id in genes
        
        RETURN count(distinct path) as paths
        """
)

# run query: `genetically interacts with` OR `RO:0002435`
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 1519
CPU times: user 5.42 ms, sys: 2.49 ms, total: 7.91 ms
Wall time: 2min 58s


In [63]:
%%time
query = (
        """
        MATCH (source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002435`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)

        WITH COLLECT(DISTINCT rna.id) + COLLECT(DISTINCT tf.id) AS genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(ph:DISO)--(g:GENE)
        
        WHERE g.id in genes AND ph.id CONTAINS 'HP:'
        
        RETURN DISTINCT ph.id AS phenotype_id, ph.preflabel AS phenotype_label, count(DISTINCT g.id) AS genes
        
        ORDER BY genes DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'phenotype_label': record['phenotype_label'],
                  'phenotype_id': record['phenotype_id'],
                  'Genes': record['genes']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 7.08 ms, sys: 5.61 ms, total: 12.7 ms
Wall time: 4min 7s


In [64]:
res_df

Genes phenotype_id                             phenotype_label
0   87     HP:0001263   Developmental disability                  
1   82     HP:0001249   intellectual disability                   
2   75     HP:0001250   epileptic seizure                         
3   60     HP:0000252   microcephaly                              
4   51     HP:0000486   strabismus                                
5   40     HP:0002650   scoliosis                                 
6   40     HP:0000508   ptosis                                    
7   39     HP:0001511   Intrauterine growth retardation           
8   35     HP:0002240   hepatomegaly                              
9   34     HP:0001744   Splenomegaly                              
10  31     HP:0000463   Anteverted nares                          
11  30     HP:0002015   Premature spillage                        
12  29     HP:0002750   Delayed skeletal maturation               
13  28     HP:0002910   Elevated transaminases                    
14  26     HP:0001252   Hypotonia                                 
15  25     HP:0000648   optic atrophy                             
16  25     HP:0009830   peripheral nervous system disease         
17  24     HP:0002019   constipation                              
18  19     HP:0000938   low femoral bone density                  
19  15     HP:0006254   Elevated alpha-fetoprotein                
20  15     HP:0001397   fatty liver disease                       
21  14     HP:0001999   Abnormal facial shape                     
22  13     HP:0001336   Myoclonus                                 
23  13     HP:0001395   liver cirrhosis                           
24  13     HP:0004325   Decreased body weight                     
25  12     HP:0001310   Dysmetria                                 
26  12     HP:0001272   Cerebellar atrophy                        
27  12     HP:0001392   Liver storage or vacuolization            
28  11     HP:0002353   EEG (electroencephalography) abnormalities
29  11     HP:0001265   hyporeflexia                              
30  10     HP:0001332   dystonia                                  
31  9      HP:0000248   brachycephaly                             
32  7      HP:0000577   exotropia                                 
33  7      HP:0000657   Oculomotor apraxia                        
34  7      HP:0001382   Joint hypermobility                       
35  7      HP:0000548   Cone/cone-rod dystrophy                   
36  7      HP:0002072   choreatic disease                         
37  6      HP:0000297   Facial hypotonia                          
38  6      HP:0002151   Increased serum lactate                   
39  6      HP:0000565   esotropia                                 
40  6      HP:0002870   obstructive sleep apnea                   
41  6      HP:0005484   Postnatal microcephaly                    
42  6      HP:0003146   Hypocholesterolemia                       
43  5      HP:0001822   Bunion                                    
44  5      HP:0000275   Narrow face                               
45  5      HP:0002673   Coxa valga                                
46  5      HP:0000966   hypohidrosis                              
47  5      HP:0200055   Small hand                                
48  5      HP:0001773   Short foot                                
49  4      HP:0012444   Brain atrophy                             
50  3      HP:0004305   movement disease                          
51  3      HP:0000539   Abnormality of refraction                 
52  2      HP:0011900   Hypofibrinogenemia                        
53  2      HP:0030043   Hip Subluxation                           
54  2      HP:0007141   Sensorimotor neuropathy                   
55  2      HP:0001649   tachycardia                               
56  2      HP:0005216   developmental delay in mastication        
57  2      HP:0012448   Delayed myelination                       
58  2      HP:0000559   Corneal scarring           

In [ ]:
%%time
query = (
        """
        MATCH (source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002435`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)

        WITH COLLECT(DISTINCT rna.id) as genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(ph:DISO)--(g:GENE)
        
        WHERE g.id in genes AND ph.id CONTAINS 'HP:'
        
        RETURN DISTINCT ph.id as phenotype_id, ph.preflabel as phenotype_label, count(DISTINCT g.id) as genes
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'phenotype_label': record['ph.preflabel'],
                  'phenotype_id': record['ph.id'],
                  'Genes': record['genes']})
    
res_df = pd.DataFrame(out_l)

In [ ]:
res_df

In [ ]:
%%time
query = (
        """
        MATCH (source:GENE)-[i1:`RO:0002434`]->(rna:GENE)-[:`RO:0002435`]-(tf:GENE)-[:`RO:0002434`]->(target:GENE)

        WITH COLLECT(DISTINCT tf.id) as genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(ph:DISO)--(g:GENE)
        
        WHERE g.id in genes AND ph.id CONTAINS 'HP:'
        
        RETURN DISTINCT ph.id as phenotype_id, ph.preflabel as phenotype_label, count(DISTINCT g.id) as genes
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'phenotype_label': record['ph.preflabel'],
                  'phenotype_id': record['ph.id'],
                  'Genes': record['genes']})
    
res_df = pd.DataFrame(out_l)

In [ ]:
res_df

---
# Without human expression data

### Specific query template with < 1000 paths => results viz graphically
Query template to answer the connection at expression level.

* in orthology relationship + genetically interacts with

In [54]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(:GENE)-[:`RO:HOM0000017`]-(:GENE)-[:`RO:0002435`]-(:GENE)-[:`RO:0002434`]->(target:GENE)

        WHERE source.id = 'FlyBase:FBgn0033050' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_uri) contains 'pubmed/29346549' AND size(interactions) <> 0

        RETURN count(distinct path) as paths
        """
)

# run query: `genetically interacts with` OR `RO:0002435`
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 4
CPU times: user 1.98 ms, sys: 0 ns, total: 1.98 ms
Wall time: 1.22 s


* in 1 to 1 orthology + interacts with

In [57]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(:GENE)-[:`RO:HOM0000020`]-(:GENE)-[:`RO:0002434`]-(:GENE)-[:`RO:0002434`]->(target:GENE)

        WHERE source.id = 'FlyBase:FBgn0033050' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_uri) contains 'pubmed/29346549' AND size(interactions) <> 0

        RETURN count(distinct path) as paths
        """
)

# run query: `genetically interacts with` OR `RO:0002435`
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 71
CPU times: user 0 ns, sys: 2.16 ms, total: 2.16 ms
Wall time: 2.53 s


* in orthology relationship + interacts with

In [58]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(:GENE)-[:`RO:HOM0000017`]-(:GENE)-[:`RO:0002434`]-(:GENE)-[:`RO:0002434`]->(target:GENE)

        WHERE source.id = 'FlyBase:FBgn0033050' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_uri) contains 'pubmed/29346549' AND size(interactions) <> 0

        RETURN count(distinct path) as paths
        """
)

# run query: `genetically interacts with` OR `RO:0002435`
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 210
CPU times: user 1.41 ms, sys: 642 µs, total: 2.05 ms
Wall time: 2.33 s


---
## Question 2

In [76]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(:GENE)-[:`RO:HOM0000017`]-(rna:GENE)-[:`RO:0002434`]-(:GENE)-[tf:`RO:0002434`]->(target:GENE)
        
        WHERE source.id = 'FlyBase:FBgn0033050' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,rna,tf,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_uri) contains 'pubmed/29346549' AND size(interactions) <> 0      

        WITH COLLECT(DISTINCT rna.id) + COLLECT(DISTINCT tf.id) AS genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(:DISO)--(g:GENE)
        
        WHERE g.id in genes
        
        RETURN count(distinct path) as paths
        """
)

# run query: `genetically interacts with` OR `RO:0002435`
result = runQuery( driver, query )

# parse results
for record in result:
    print('Paths: {}'.format(record['paths']))

Paths: 60
CPU times: user 1.35 ms, sys: 607 µs, total: 1.96 ms
Wall time: 2.69 s


In [77]:
%%time
query = (
        """
        MATCH path=(source:GENE)-[i1:`RO:0002434`]->(:GENE)-[:`RO:HOM0000017`]-(rna:GENE)-[:`RO:0002434`]-(:GENE)-[tf:`RO:0002434`]->(target:GENE)
        
        WHERE source.id = 'FlyBase:FBgn0033050' AND target.id = 'HGNC:633' AND ALL(x IN nodes(path) WHERE single(y IN nodes(path) WHERE y = x))

        WITH path,i1,rna,tf,

        [n IN nodes(path) WHERE n.preflabel IN ['cytoplasm','cytosol','nucleus','metabolism','membrane','protein binding','visible','viable','phenotype']] AS nodes_marked,

        [r IN relationships(path) WHERE toLower(r.reference_supporting_text) =~ '.*tftargets.*|.*msigdb.*'] AS interactions

        WHERE size(nodes_marked) = 0 AND toLower(i1.reference_uri) contains 'pubmed/29346549' AND size(interactions) <> 0      

        WITH COLLECT(DISTINCT rna.id) + COLLECT(DISTINCT tf.id) AS genes
        
        MATCH path=(:DISO {id: 'DOID:0060728'})-->(ph:DISO)--(g:GENE)
        
        WHERE g.id in genes AND ph.id CONTAINS 'HP:'
        
        RETURN DISTINCT ph.id AS phenotype_id, ph.preflabel AS phenotype_label, COLLECT(DISTINCT g.name) AS gene_id_list, count(DISTINCT g.id) AS genes
        
        ORDER BY genes DESC
        """
)

# run query
result = runQuery( driver, query )

# parse results
out_l = list()
for record in result:
    out_l.append({'phenotype_label': record['phenotype_label'],
                  'phenotype_id': record['phenotype_id'],
                  'gene_id_list': record['gene_id_list'],
                  'genes': record['genes']})
    
res_df = pd.DataFrame(out_l)

CPU times: user 730 µs, sys: 2.72 ms, total: 3.45 ms
Wall time: 2.68 s


In [78]:
res_df

gene_id_list  \
0   [ELOVL fatty acid elongase 4, membrane metalloendopeptidase, glutamate ionotropic receptor AMPA type subunit 3, heat shock protein family B (small) member 1]   
1   [MYCN proto-oncogene, bHLH transcription factor, UDP-galactose-4-epimerase, ELOVL fatty acid elongase 4]                                                        
2   [glutamate ionotropic receptor AMPA type subunit 3, UDP-galactose-4-epimerase, MYCN proto-oncogene, bHLH transcription factor]                                  
3   [glutamate ionotropic receptor AMPA type subunit 3, serpin family I member 1, MYCN proto-oncogene, bHLH transcription factor]                                   
4   [3-hydroxyacyl-CoA dehydratase 1, serpin family H member 1, endothelin converting enzyme like 1]                                                                
5   [lysozyme, UDP-galactose-4-epimerase]                                                                                                                           
6   [ELOVL fatty acid elongase 4, MYCN proto-oncogene, bHLH transcription factor]                                                                                   
7   [lysozyme, UDP-galactose-4-epimerase]                                                                                                                           
8   [3-hydroxyacyl-CoA dehydratase 1, UDP-galactose-4-epimerase]                                                                                                    
9   [ELOVL fatty acid elongase 4, membrane metalloendopeptidase]                                                                                                    
10  [MYCN proto-oncogene, bHLH transcription factor, endothelin converting enzyme like 1]                                                                           
11  [glutamate ionotropic receptor AMPA type subunit 3, serpin family I member 1]                                                                                   
12  [glutamate ionotropic receptor AMPA type subunit 3]                                                                                                             
13  [3-hydroxyacyl-CoA dehydratase 1]                                                                                                                               
14  [ELOVL fatty acid elongase 4]                                                                                                                                   
15  [MYCN proto-oncogene, bHLH transcription factor]                                                                                                                
16  [heat shock protein family B (small) member 1]                                                                                                                  
17  [serpin family H member 1]                                                                                                                                      
18  [MYCN proto-oncogene, bHLH transcription factor]                                                                                                                
19  [3-hydroxyacyl-CoA dehydratase 1]                                                                                                                               
20  [ELOVL fatty acid elongase 4]                                                                                                                                   
21  [3-hydroxyacyl-CoA dehydratase 1]                                                                                                                               
22  [ELOVL fatty acid elongase 4]                                                                                                                                   
23  [ELOVL fatty acid elongase 4]                                                                                                                                   

    genes phenotype_id 